In [1]:
%load_ext autoreload
%autoreload 2

import pandas as pd
import os
import numpy as np
from scipy.optimize import minimize
from scipy.io import loadmat
from Likelihood import Likelihood
from functools import partial

In [2]:
def load_csv(filename, folder):
    return pd.read_csv(os.path.join(folder, f"{filename}.csv"), header=0).values

folder = "/Users/emmaknippel/Desktop/POLIT 10 SEM/Dynamic Programming/Replicating the Innovators Dilemma/1 Summary Statistics/Data"
State = load_csv("State", folder)
Adopt = load_csv("Adopt", folder)
Exit = load_csv("Exit", folder)

Pi = loadmat('CheckPi.mat')['Pi']

In [5]:
T = Pi.shape[0]
beta = 0.80      # Discount factor
delta = 1.10   # Decline in SC
scaling = 10000   # Scaling factor
iterMLE = 1

print(f"  -----------------------------------------")
print(f" | STRATEGIC (RATIONAL-EXPECTATIONS) MODEL |")
print(f"  -----------------------------------------")

print(f" ----- Basic parameters to be \"calibrated\" -----")
print(f"   Profit/value scaling      :     {scaling:4.0f}")
print(f"   Discount factor (beta)    :     {beta:1.4f}")
print(f"   Adoption cost drop (delta):     {delta:1.4f}")
print(" -----------------------------------------------\n")

# Rescale profits
Pi = Pi / scaling

# Terminal Values
V = np.zeros((T, 3, 12, 12, 15))
V[T-1,:,:,:,:] = Pi[T-1,:,:,:,:] / (1 - beta)

# Initialize Solutions
EV = np.zeros((T, 5, 12, 12, 15))
Policy = np.zeros((T-1, 5, 12, 12, 15))

# MLE Estimation
x0 = [1, 1, 1]
options = {'disp': True, 'maxiter': 1000, 'xatol': 1e-4, 'fatol': 1e-8}

objective_function = partial(Likelihood, beta=beta, delta=delta, Pi=Pi, V=V, EV=EV, Policy=Policy, State=State, Exit=Exit, Adopt=Adopt, T=T, iterMLE=iterMLE, output_type=1)

res = minimize(objective_function, x0, method='Nelder-Mead', options=options)
Theta = res.x

# Numerical derivatives for standard errors
perturb = 0.001
logL = Likelihood(Theta, 2)
logLderiv = np.zeros((1, 3))

for k in range(3):
    Theta_perturbed = np.copy(Theta)
    Theta_perturbed[k] += perturb
    logL_perturbed = Likelihood(Theta_perturbed, 2)
    logLderiv[0, k] = (logL_perturbed - logL) / perturb

# Derive the Value estimate
Vhat = np.linalg.inv(logLderiv.T @ logLderiv)

print(f"\n ----- Maximum Likelihood Estimation Results for (phi & kappa_inc) -----")
print(f" Coeff.: " + " ".join([f"{v:8.8f}" for v in Theta]))
print(f" S.E.  : " + " ".join([f"{v:8.8f}" for v in np.sqrt(np.diag(Vhat))]))
print(f" -----------------------------------------------------------------------\n")

  -----------------------------------------
 | STRATEGIC (RATIONAL-EXPECTATIONS) MODEL |
  -----------------------------------------
 ----- Basic parameters to be "calibrated" -----
   Profit/value scaling      :     1000
   Discount factor (beta)    :     0.8000
   Adoption cost drop (delta):     1.1000
 -----------------------------------------------


MLE iter #   1: trying (phi, kappa_inc, kappa_ent) = (1.00000000, 1.00000000, 1.00000000)
Year: 16, State    1: (no, nb, nn) = ( 0,  0,  0)
Expected Value (z1, z2, z3, z4, z5) = (0.00, 0.00, 0.00, 0.00, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, 0.0000, 0.0000, 0.0000, 0.0000)
Value today (Vo, Vb, Vn) = (0.00, 0.00, 0.00)
Year: 16, State    2: (no, nb, nn) = ( 0,  0,  1)
Expected Value (z1, z2, z3, z4, z5) = (0.00, 0.00, 0.00, 0.00, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, 0.0000, 0.0000, 0.2689, 0.0000)
Value today (Vo, Vb, Vn) = (0.00, 0.00, 1.89)
Year: 16, State    3: (no, nb, nn) = ( 0,  0,  2)
E

/Users/emmaknippel/Desktop/POLIT 10 SEM/Dynamic Programming/Term Paper/ReplicatingInnovatorsDilemma/3 Maximum Likelihood/fun8.py:16: RuntimeWarning: overflow encountered in exp
  stay = np.exp(phi + beta * z3)


Year: 11, State   43: (no, nb, nn) = ( 0,  2, 12)
Expected Value (z1, z2, z3, z4, z5) = (0.00, 0.00, 40.54, 40.07, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, 0.0000, 0.0019, 0.0019, 0.0000)
Value today (Vo, Vb, Vn) = (0.00, 34.01, 33.64)
Year: 11, State   44: (no, nb, nn) = ( 0,  2, 13)
Expected Value (z1, z2, z3, z4, z5) = (0.00, 0.00, 41.60, 40.73, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, 0.0000, 0.0019, 0.0019, 0.0000)
Value today (Vo, Vb, Vn) = (0.00, 34.86, 34.16)
Year: 11, State   45: (no, nb, nn) = ( 0,  2, 14)
Expected Value (z1, z2, z3, z4, z5) = (0.00, 0.00, 41.77, 40.80, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, 0.0000, 0.0019, 0.0019, 0.0000)
Value today (Vo, Vb, Vn) = (0.00, 34.99, 34.22)
Year: 11, State   46: (no, nb, nn) = ( 0,  3,  0)
Expected Value (z1, z2, z3, z4, z5) = (0.00, 0.00, 428.99, 0.00, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, 0.0000, 0.0019, 0.0000, 0.0000)
Value today (Vo, Vb, Vn) = (

/Users/emmaknippel/Desktop/POLIT 10 SEM/Dynamic Programming/Term Paper/ReplicatingInnovatorsDilemma/3 Maximum Likelihood/fun12.py:15: RuntimeWarning: overflow encountered in exp
  stay = np.exp(phi + beta * z3)


Year: 11, State 2012: (no, nb, nn) = (11,  2,  1)
Expected Value (z1, z2, z3, z4, z5) = (10.90, 6.27, 39.91, 37.79, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0001, 0.0015, 0.0019, 0.0019, 0.0000)
Value today (Vo, Vb, Vn) = (10.30, 33.51, 31.81)
Year: 11, State 2013: (no, nb, nn) = (11,  2,  2)
Expected Value (z1, z2, z3, z4, z5) = (10.96, 5.51, 39.38, 38.97, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0001, 0.0010, 0.0019, 0.0019, 0.0000)
Value today (Vo, Vb, Vn) = (10.35, 33.08, 32.75)
Year: 11, State 2014: (no, nb, nn) = (11,  2,  3)
Expected Value (z1, z2, z3, z4, z5) = (10.96, 5.51, 39.43, 39.02, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0001, 0.0010, 0.0019, 0.0019, 0.0000)
Value today (Vo, Vb, Vn) = (10.35, 33.12, 32.79)
Year: 11, State 2015: (no, nb, nn) = (11,  2,  4)
Expected Value (z1, z2, z3, z4, z5) = (10.96, 5.51, 39.43, 39.02, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0001, 0.0010, 0.0019, 0.0019, 0.0000)
Value today (Vo, Vb, 

...

/Users/emmaknippel/Desktop/POLIT 10 SEM/Dynamic Programming/Term Paper/ReplicatingInnovatorsDilemma/3 Maximum Likelihood/fun2.py:115: RuntimeWarning: invalid value encountered in double_scalars
  EV2 += BS2[no_prime + 11*nb_prime + (11*11)*nn_prime + (11*11*14)*npe_prime] \


Year: 10, State  207: (no, nb, nn) = ( 1,  1, 11)
Expected Value (z1, z2, z3, z4, z5) = (55.96, nan, nan, nan, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (nan, nan, nan, nan, 0.0000)
Value today (Vo, Vb, Vn) = (nan, nan, nan)
Year: 10, State  208: (no, nb, nn) = ( 1,  1, 12)
Expected Value (z1, z2, z3, z4, z5) = (124.32, nan, nan, nan, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (nan, nan, nan, nan, 0.0000)
Value today (Vo, Vb, Vn) = (nan, nan, nan)
Year: 10, State  209: (no, nb, nn) = ( 1,  1, 13)
Expected Value (z1, z2, z3, z4, z5) = (181.84, nan, nan, nan, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (nan, nan, nan, nan, 0.0000)
Value today (Vo, Vb, Vn) = (nan, nan, nan)
Year: 10, State  210: (no, nb, nn) = ( 1,  1, 14)
Expected Value (z1, z2, z3, z4, z5) = (345.23, nan, nan, nan, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (nan, nan, nan, nan, 0.0000)
Value today (Vo, Vb, Vn) = (nan, nan, nan)
Year: 10, State  211: (no, nb, nn) = ( 1,  2,  0)
Expected Va

/Users/emmaknippel/Desktop/POLIT 10 SEM/Dynamic Programming/Term Paper/ReplicatingInnovatorsDilemma/3 Maximum Likelihood/fun7.py:23: RuntimeWarning: invalid value encountered in double_scalars
  z7 = adopt / (np.exp(0) + stay + adopt)


Year: 10, State  498: (no, nb, nn) = ( 2,  9,  2)
Expected Value (z1, z2, z3, z4, z5) = (14.50, inf, nan, nan, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, nan, nan, nan, 0.0000)
Value today (Vo, Vb, Vn) = (inf, nan, nan)
Year: 10, State  499: (no, nb, nn) = ( 2,  9,  3)
Expected Value (z1, z2, z3, z4, z5) = (14.47, inf, nan, nan, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, nan, nan, nan, 0.0000)
Value today (Vo, Vb, Vn) = (inf, nan, nan)
Year: 10, State  500: (no, nb, nn) = ( 2,  9,  4)
Expected Value (z1, z2, z3, z4, z5) = (14.40, inf, nan, nan, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, nan, nan, nan, 0.0000)
Value today (Vo, Vb, Vn) = (inf, nan, nan)
Year: 10, State  501: (no, nb, nn) = ( 2,  9,  5)
Expected Value (z1, z2, z3, z4, z5) = (14.29, inf, nan, nan, 0.00)
Choice Probabilities (z6, z7, z8, z9, z10) = (0.0000, nan, nan, nan, 0.0000)
Value today (Vo, Vb, Vn) = (inf, nan, nan)
Year: 10, State  502: (no, nb, nn) = ( 2,  9,  6)
Ex

Warning: Error fun1: Vprime must have 6480 elements